In [2]:
from io import StringIO
from scipy import stats
from scipy.interpolate import interp1d
from scipy.signal import hilbert, chirp

import seaborn as sns
import pyaudio
import wave
import matplotlib.pyplot as plt
import numpy as np
import plotly.express as px

In [3]:
sample_format = pyaudio.paInt16  # 16 bits per sample
CHANNELS = 2
RATE = 44100
COUNT = 4
CHUNK = int(RATE / COUNT) # 1024 int(RATE / 4)
TRESHHOLD = 2000
seconds = 2
filename = "output.wav"

In [4]:
def get_medians_from_frame(frame):
    medians = []
    for f in frame:
        medians.append(np.median(frame))
    return medians

In [5]:
def get_squares(frame):
    new_frames = []
    for f in frame:
        new_frames.append(
            # f ** 2
            abs(f)
        )
    return new_frames

In [6]:
def moving_avg(x, n):
 cumsum = np.cumsum(np.insert(x, 0, 0)) 
 return (cumsum[n:] - cumsum[:-n]) / float(n)

In [11]:
def plot(frame):
    fig = px.line(np.array(frame))
    fig.show()

In [12]:
# data = np.concatenate(frames)
def process(frame):
    print(f"frame = {frame}")
    # data = np.concatenate(frames)
    # for i in range(len(frames) - COUNT):
    #     print(np.concatenate(frames[i:i+COUNT]))
    # print(get_medians_from_frame(frame))
    frame = get_squares(frame)
    frame = moving_avg(frame, int(CHUNK / 2))
    print(f"moving_avg = {frame}")
    plot(frame)
    return frame

=====

In [16]:
p = pyaudio.PyAudio()

stream = p.open(format=pyaudio.paInt16, channels=CHANNELS, rate=RATE, input=True,  frames_per_buffer=CHUNK)
frames = []
global_frames = []

print("Listening...")
for i in range(0, int(RATE / CHUNK * seconds)):
    sample = stream.read(CHUNK)
    frame = np.fromstring(sample, dtype=np.int16)
    frames.append(frame)
    global_frames.append(frame)
    print(len(frames))
    if len(frames) % COUNT == 0:
        # print("Cough?")
        # by_one_seconds_frame = np.concatenate(frames)
        # print(ln(by_one_seconds_frame))
        process(frames)
    # plot(frame)

        # plot(frames[i])
        frames = []
        
stream.stop_stream()
stream.close()
p.terminate()

# save
wf = wave.open(filename, 'wb')
wf.setnchannels(CHANNELS)
wf.setsampwidth(p.get_sample_size(sample_format))
wf.setframerate(RATE)
wf.writeframes(b''.join(frames))
wf.close()

ALSA lib pcm.c:2664:(snd_pcm_open_noupdate) Unknown PCM cards.pcm.rear
ALSA lib pcm.c:2664:(snd_pcm_open_noupdate) Unknown PCM cards.pcm.center_lfe
ALSA lib pcm.c:2664:(snd_pcm_open_noupdate) Unknown PCM cards.pcm.side
ALSA lib pcm_route.c:877:(find_matching_chmap) Found no matching channel map
ALSA lib pcm_route.c:877:(find_matching_chmap) Found no matching channel map
ALSA lib pcm_route.c:877:(find_matching_chmap) Found no matching channel map
ALSA lib pcm_route.c:877:(find_matching_chmap) Found no matching channel map
ALSA lib pcm_oss.c:397:(_snd_pcm_oss_open) Cannot open device /dev/dsp
ALSA lib pcm_oss.c:397:(_snd_pcm_oss_open) Cannot open device /dev/dsp
ALSA lib confmisc.c:160:(snd_config_get_card) Invalid field card
ALSA lib pcm_usb_stream.c:482:(_snd_pcm_usb_stream_open) Invalid card 'card'
ALSA lib confmisc.c:160:(snd_config_get_card) Invalid field card
ALSA lib pcm_usb_stream.c:482:(_snd_pcm_usb_stream_open) Invalid card 'card'


Listening...


/tmp/ipykernel_20297/2270611521.py:10: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead



1
2
3
4
frame = [array([58, 58, 60, ..., 11, 19, 19], dtype=int16), array([ 23,  23,  14, ..., -89, -83, -83], dtype=int16), array([  -78,   -78,   -82, ..., 14083, 10840, 10840], dtype=int16), array([ 3759,  3759, -1482, ...,  -397,  -423,  -423], dtype=int16)]
moving_avg = [  46.1063135    46.09760522   46.08889695 ... 1622.03628447 1621.90348331
 1621.77068215]


/tmp/ipykernel_20297/2270611521.py:10: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead



1
2
3
4
frame = [array([-331, -331,  -38, ...,    9,   -5,   -5], dtype=int16), array([  0,   0,   5, ..., 108, 139, 139], dtype=int16), array([ 152,  152,  175, ..., -524, -725, -725], dtype=int16), array([ -912,  -912, -1288, ...,   -15,   -14,   -14], dtype=int16)]
moving_avg = [619.28918723 619.24473875 619.20029028 ... 128.2703193  128.25217707
 128.23403483]


In [226]:
global_frames

[array([42, 42, 33, ...,  5, -7, -7], dtype=int16),
 array([ -9,  -9,  -6, ..., 565, 538, 538], dtype=int16),
 array([532, 532, 466, ..., -20, -25, -25], dtype=int16),
 array([-24, -24, -27, ...,  14,  17,  17], dtype=int16),
 array([17, 17, 19, ..., 14, 16, 16], dtype=int16),
 array([14, 14,  6, ..., 45, 51, 51], dtype=int16),
 array([ 37,  37,  34, ..., -28, -24, -24], dtype=int16),
 array([-21, -21, -12, ..., -44, -61, -61], dtype=int16)]

In [182]:
d = [1, 2, 3, 4, 5, 6, 7, 8]
for i in range(0, len(d) - 4):
    print(d[i], d[i + 4])

1 5
2 6
3 7
4 8
